In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import shap
import os
import pickle

In [2]:
# Set working dir
os.chdir('/users/rg/dgarrido/PhD/projects/side_tasks/chrom_bea/nf/ml-nf/')

In [3]:
# Gene subset of interest
sub_f = "data/subset/upregulated.bed"
sub = pd.read_csv(sub_f, sep = "\t", header = None)[3]
sub = sub.str.replace("\..*", "")
sub

0       ENSG00000078808
1       ENSG00000008130
2       ENSG00000157933
3       ENSG00000157916
4       ENSG00000157873
             ...       
2098    ENSG00000160211
2099    ENSG00000269335
2100    ENSG00000160219
2101    ENSG00000185515
2102    ENSG00000124333
Name: 3, Length: 2103, dtype: object

In [4]:
# Expression data
expr_f = "data/gene.expression.tsv"
expr = pd.read_csv(expr_f, sep = "\t")
timepoints = expr.columns.tolist()
expr

H000  H003  H006  H009  H012  H018  H024  H036  H048  H072  \
ENSG00000000419  6.14  6.11  6.18  6.29  6.29  6.15  6.22  6.17  6.42  6.24   
ENSG00000000457  2.37  2.21  2.59  2.63  2.59  2.38  2.45  2.49  2.64  2.74   
ENSG00000000460  3.91  3.47  3.72  4.05  3.94  3.95  3.95  3.99  3.87  2.84   
ENSG00000000938  0.66  0.51  0.38  0.31  0.40  0.84  1.34  4.10  5.29  5.93   
ENSG00000000971  0.44  0.45  0.72  0.91  1.40  1.96  2.54  2.77  3.15  3.87   
...               ...   ...   ...   ...   ...   ...   ...   ...   ...   ...   
ENSGR0000196433  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00   
ENSGR0000197976  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00   
ENSGR0000198223  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00   
ENSGR0000205755  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00   
ENSGR0000214717  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00  0.00   

                 H120  H168  
ENSG00000000419  5.74  5.51  
ENSG00000000457  2.69  2.85  
ENSG00000000460  2.29  2.48  
ENSG00000000938  5.99  5.26  
ENSG00000000971  3.57  3.38  
...               ...   ...  
ENSGR0000196433  0.00  0.00  
ENSGR0000197976  0.00  0.00  
ENSGR0000198223  0.00  0.00  
ENSGR0000205755  0.00  0.00  
ENSGR0000214717  0.00  0.00  

[12248 rows x 12 columns]

In [5]:
# Chromatin data
marks_f = "data/marks.txt"
marks_dir = "data/marks"
marks = pd.read_csv(marks_f, sep = "\t", header = None, squeeze = True)

chrom = pd.read_csv("%s/%s.tsv" % (marks_dir, marks[0]), sep = "\t")
chrom.columns = [marks[0] + "_" + i for i in chrom.columns]

for mark in marks[1:]:
    tmp =  pd.read_csv("%s/%s.tsv" % (marks_dir, mark), sep = "\t")
    tmp.columns = [mark + "_" + i for i in tmp.columns]
    chrom = chrom.join(tmp)
chrom

H3K4me3_H000  H3K4me3_H003  H3K4me3_H006  H3K4me3_H009  \
ENSG00000000005          0.06          0.06          0.06          0.06   
ENSG00000000419          3.75          3.72          3.87          4.10   
ENSG00000000457          2.96          2.87          2.94          2.68   
ENSG00000000460          2.90          3.16          3.43          3.24   
ENSG00000000938          0.99          1.11          0.99          1.15   
...                       ...           ...           ...           ...   
ENSGR0000196433          0.00          0.00          0.00          0.00   
ENSGR0000197976          0.00          0.00          0.00          0.00   
ENSGR0000198223          0.00          0.00          0.00          0.00   
ENSGR0000205755          0.00          0.00          0.00          0.00   
ENSGR0000214717          0.00          0.00          0.00          0.00   

                 H3K4me3_H012  H3K4me3_H018  H3K4me3_H024  H3K4me3_H036  \
ENSG00000000005          0.06          0.07          0.07          0.05   
ENSG00000000419          3.92          3.84          3.62          3.97   
ENSG00000000457          2.81          3.20          2.69          2.84   
ENSG00000000460          3.28          3.08          3.13          2.98   
ENSG00000000938          1.09          1.07          1.09          1.19   
...                       ...           ...           ...           ...   
ENSGR0000196433          0.00          0.00          0.00          0.00   
ENSGR0000197976          0.00          0.00          0.00          0.00   
ENSGR0000198223          0.00          0.00          0.00          0.00   
ENSGR0000205755          0.00          0.00          0.00          0.00   
ENSGR0000214717          0.00          0.00          0.00          0.00   

                 H3K4me3_H048  H3K4me3_H072  ...  H4K20me1_H006  \
ENSG00000000005          0.06          0.06  ...           0.09   
ENSG00000000419          3.72          3.14  ...           0.45   
ENSG00000000457          2.69          2.83  ...           0.10   
ENSG00000000460          3.17          2.94  ...           0.06   
ENSG00000000938          1.59          2.64  ...           0.08   
...                       ...           ...  ...            ...   
ENSGR0000196433          0.00          0.00  ...           0.00   
ENSGR0000197976          0.00          0.00  ...           0.00   
ENSGR0000198223          0.00          0.00  ...           0.00   
ENSGR0000205755          0.00          0.00  ...           0.00   
ENSGR0000214717          0.00          0.00  ...           0.00   

                 H4K20me1_H009  H4K20me1_H012  H4K20me1_H018  H4K20me1_H024  \
ENSG00000000005           0.08           0.08           0.10           0.08   
ENSG00000000419           0.44           0.39           0.44           0.42   
ENSG00000000457           0.11           0.12           0.14           0.13   
ENSG00000000460           0.07           0.07           0.07           0.07   
ENSG00000000938           0.08           0.07           0.07           0.06   
...                        ...            ...            ...            ...   
ENSGR0000196433           0.00           0.00           0.00           0.00   
ENSGR0000197976           0.00           0.00           0.00           0.00   
ENSGR0000198223           0.00           0.00           0.00           0.00   
ENSGR0000205755           0.00           0.00           0.00           0.00   
ENSGR0000214717           0.00           0.00           0.00           0.00   

                 H4K20me1_H036  H4K20me1_H048  H4K20me1_H072  H4K20me1_H120  \
ENSG00000000005           0.11           0.11           0.09           0.08   
ENSG00000000419           0.39           0.36           0.39           0.42   
ENSG00000000457           0.13           0.12           0.12           0.24   
ENSG00000000460           0.06           0.06           0.06           0.07   
ENSG00000000938           0.07           0.08           0.30      

In [6]:
# Data matrices / load / save predictions
X0 = chrom.loc[sub,]
Y = expr.loc[sub,]  

for tpselx in timepoints:
    for tpsely in timepoints:
        print (tpselx, tpsely)
        with open("result.upreg/%s_%s/model.pickle" % (tpselx, tpsely), 'rb') as f:
            rfc_best = pickle.load(f)
        f.close()
        X = X0.filter(like = tpselx, axis = 1)
        X.columns = X.columns.str.replace("_.*", "")
        y = Y[tpsely]
        p = rfc_best.predict(X)
        out = pd.concat([pd.Series(p, index = X.index), y], axis = 1)
        out.to_csv("result.upreg/%s_%s/predVSreal.txt" % (tpselx, tpsely), sep="\t", header=False)


H000 H000


Trying to unpickle estimator DecisionTreeRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
Trying to unpickle estimator RandomForestRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.


H000 H003


Trying to unpickle estimator DecisionTreeRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
Trying to unpickle estimator RandomForestRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.


H000 H006


...

Trying to unpickle estimator DecisionTreeRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
Trying to unpickle estimator RandomForestRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.


H168 H120


Trying to unpickle estimator DecisionTreeRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
Trying to unpickle estimator RandomForestRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.


H168 H168


Trying to unpickle estimator DecisionTreeRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
Trying to unpickle estimator RandomForestRegressor from version 0.23.2 when using version 0.23.1. This might lead to breaking code or invalid results. Use at your own risk.
